<h1><center>Laboratorio 9:  ¿Superhéroe o Villano?  🦴</center></h1>

<center><strong>MDS7202: Laboratorio de Programación Científica para Ciencia de Datos</strong></center>

### Cuerpo Docente:

- Profesor: Pablo Badilla y Ignacio Meza
- Auxiliar: Sebastián Tinoco
- Ayudante: Felipe Arias y Diego Cortez

### Equipo: SUPER IMPORTANTE - notebooks sin nombre no serán revisados

- Nombre de alumno 1: Lennin Chamorro
- Nombre de alumno 2: Martín Reyes Oviedo


### **Link de repositorio de GitHub:** https://github.com/Landilus/Lab_prog_cientifica

## Temas a tratar

- Codificación de texto usando Bag of Words.
- Búsqueda del modelo óptimo de clasificación usando `GridSearch`
- Uso de pipelines.

## Reglas:

- **Grupos de 2 personas**
- Asistencia **obligatoria** a instrucciones del lab (viernes 16.15). Luego, pueden quedarse trabajando en las salas o irse.
- **No se revisarán entregas de personas ausentes**.
- Cualquier duda fuera del horario de clases al foro. Mensajes al equipo docente serán respondidos por este medio.
- Prohibidas las copias.
- Pueden usar cualquer material del curso que estimen conveniente.

### Objetivos principales del laboratorio

- Obtener caracteristicas a partir de texto usando `CountVectorizer`.
- Fijar un pipeline con un modelo base que luego se irá optimizando.
- Comprender como realizar una búsqueda de grilla sobre un conjunto de clasificadores e hiperparámetros usando `GridSearch`.

El laboratorio deberá ser desarrollado sin el uso indiscriminado de iteradores nativos de python (aka "for", "while"). La idea es que aprendan a exprimir al máximo las funciones optimizadas que nos entrega `pandas`, las cuales vale mencionar, son bastante más eficientes que los iteradores nativos sobre DataFrames.

#Importamos librerias utiles 😸

In [ ]:
# Librería Core del lab.
import numpy as np
import pandas as pd
from sklearn.pipeline import Pipeline

from sklearn.model_selection import train_test_split

# Pre-procesamiento
from sklearn.feature_selection import SelectPercentile, f_classif
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import MinMaxScaler
from sklearn.feature_extraction.text import CountVectorizer


# Clasifación
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression

# Metricas de evaluación
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
from sklearn.metrics import cohen_kappa_score

# Librería para plotear
!pip install --upgrade plotly
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# Proyecciones en baja dimensionalidad: UMAP
!pip install umap-learn

# Librería para NLP
!pip install nltk
import nltk
from nltk.corpus import stopwords
from nltk import word_tokenize
from nltk.stem import PorterStemmer
nltk.download('stopwords')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\marti\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\marti\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

# 1. ¿Quien es Bat Cow?

<p align="center">
  <img src="https://i.imgur.com/D9f1RHy.jpg" width="350">
</p>

En vez de estar desarrollando las evaluaciones correspondientes a su curso, su profesor de catedra y su auxiliar discuten acerca la alineación (héroe o villano) del personaje de ficción Bat-Cow.

El cuerpo docente, no logra ponerse de acuerdo si el personaje es bueno, neutral o malo: el auxiliar plantea que Bat-cow posee una siniestra mirada, intrigante pero común característica de los personajes malvados.
Por otra parte, extendiendo las ideas de Rousseau, el profesor plantea que tal como los humanos no nacen malos, no existe motivo por el cual una vaca con superpoderes deba serlo.

Sin embargo, ambos concuerdan que es difícil estimar la alineación solo usando los atributos físicos, por lo que creen el análisis debe ser complementado aún más antes de comunicarle los resultados a su estudiantado. Buscando más información, ambos sujetos se percatan de la existencia de un excelente antecedente para estimar la alineación: la historia personal de cada superhéroe o villano.

Es por esto le solicitan que construya y optimice un clasificador basado en texto el cual analice la alineación de cada personaje basado en su historia personal.

Para este laboratorio deben trabajar con los datos `df_comics.csv` y `comics_no_label.csv` subidos a u-cursos. El primero es un conjunto de datos que les servirá para entrenar un modelo de clasificación, mientras que el segundo es un dataset con personajes de ficción no etiquetados a predecir (sí, aquí está la misteriosa Batcow).

Para comenzar cargue los dataset señalados y visualice a través de un head los atributos que poseen cada uno de los dataset.


In [ ]:
# Si usted está utilizando Colaboratory le puede ser útil este código para cargar los archivos.
try:
    from google.colab import drive
    drive.mount("/content/drive")
    path = 'Dirección donde tiene los archivos en el Drive'
except:
    print('Ignorando conexión drive-colab')

Ignorando conexión drive-colab


In [ ]:
df_comics = pd.read_csv('df_comics.csv')
df_comics_no_label = pd.read_csv('comics_no_label.csv')
df_comics = df_comics.dropna(subset=['history_text']) # eliminar ejemplos sin historia

In [ ]:
df_comics = pd.read_csv('C:/Users/marti/Desktop/Universidad/IX_Semestre/LPC/Lab_09/df_comics.csv')
df_comics_no_label = pd.read_csv('C:/Users/marti/Desktop/Universidad/IX_Semestre/LPC/Lab_09/comics_no_label.csv')
df_comics = df_comics.dropna(subset=['history_text']) # eliminar ejemplos sin historia

In [ ]:
df_comics.head(5)

Unnamed: 0          name               real_name               full_name  \
0           0       3-D Man     Delroy Garrett, Jr.     Delroy Garrett, Jr.   
1           2        A-Bomb  Richard Milhouse Jones  Richard Milhouse Jones   
2           3            Aa                      Aa                     NaN   
3           4    Aaron Cash              Aaron Cash              Aaron Cash   
4           5  Aayla Secura            Aayla Secura                     NaN   

  overall_score                                       history_text  \
0             6  Delroy Garrett, Jr. grew up to become a track ...   
1            20   Richard "Rick" Jones was orphaned at a young ...   
2            12  Aa is one of the more passive members of the P...   
3             5  Aaron Cash is the head of security at Arkham A...   
4             8  ayla Secura was a Rutian Twi'lek Jedi Knight (...   

                                         powers_text  intelligence_score  \
0                                                NaN                  85   
1    On rare occasions, and through unusual circu...                  80   
2                                                NaN                  80   
3                                                NaN                  80   
4                                                NaN                  90   

   strength_score  speed_score  ...  has_flight  has_accelerated_healing  \
0              30           60  ...         0.0                      0.0   
1             100           80  ...         0.0                      1.0   
2              50           55  ...         0.0                      0.0   
3              10           25  ...         0.0                      0.0   
4              40           45  ...         0.0                      1.0   

   has_weapons_master has_intelligence has_reflexes has_super_speed  \
0                 0.0              0.0          0.0             1.0   
1                 0.0              0.0          1.0             1.0   
2                 0.0              0.0          0.0             0.0   
3                 1.0              0.0          0.0             0.0   
4                 0.0              0.0          0.0             0.0   

  has_durability has_stamina has_agility has_super_strength  
0            0.0         0.0         0.0                1.0  
1            1.0         1.0         1.0                1.0  
2            0.0         0.0         0.0                0.0  
3            0.0         0.0         0.0                0.0  
4            0.0         0.0         1.0                0.0  

[5 rows x 82 columns]

In [ ]:
df_comics.describe()

Unnamed: 0  intelligence_score  strength_score  speed_score  \
count  1285.000000         1285.000000     1285.000000  1285.000000   
mean    727.744747           78.665370       38.832685    45.898833   
std     415.297480           25.074439       34.220845    29.176614   
min       0.000000            0.000000        0.000000     0.000000   
25%     372.000000           75.000000       10.000000    25.000000   
50%     728.000000           85.000000       30.000000    40.000000   
75%    1084.000000           95.000000       65.000000    65.000000   
max    1449.000000          100.000000      100.000000   100.000000   

       durability_score  power_score  combat_score  has_electrokinesis  \
count       1285.000000  1285.000000   1285.000000         1228.000000   
mean          55.610895    66.556420     67.805447            0.089577   
std           31.683003    33.329484     29.598315            0.285690   
min            0.000000     0.000000      0.000000            0.000000   
25%           30.000000    40.000000     55.000000            0.000000   
50%           55.000000    70.000000     75.000000            0.000000   
75%           85.000000   100.000000     90.000000            0.000000   
max          100.000000   100.000000    100.000000            1.000000   

       has_energy_constructs  has_mind_control_resistance  ...   has_flight  \
count            1228.000000                  1228.000000  ...  1228.000000   
mean                0.074919                     0.074104  ...     0.265472   
std                 0.263367                     0.262047  ...     0.441764   
min                 0.000000                     0.000000  ...     0.000000   
25%                 0.000000                     0.000000  ...     0.000000   
50%                 0.000000                     0.000000  ...     0.000000   
75%                 0.000000                     0.000000  ...     1.000000   
max                 1.000000                     1.000000  ...     1.000000   

       has_accelerated_healing  has_weapons_master  has_intelligence  \
count              1228.000000         1228.000000       1228.000000   
mean                  0.307003            0.403909          0.429153   
std                   0.461439            0.490880          0.495157   
min                   0.000000            0.000000          0.000000   
25%                   0.000000            0.000000          0.000000   
50%                   0.000000            0.000000          0.000000   
75%                   1.000000            1.000000          1.000000   
max                   1.000000            1.000000          1.000000   

       has_reflexes  has_super_speed  has_durability  has_stamina  \
count   1228.000000      1228.000000     1228.000000  1228.000000   
mean       0.437296         0.387622        0.504886     0.540717   
std        0.496255         0.487406        0.500180     0.498542   
min        0.000000         0.000000        0.000000     0.000000   
25%        0.000000         0.000000        0.000000     0.000000   
50%        0.000000         0.000000        1.000000     1.000000   
75%        1.000000         1.000000        1.000000     1.000000   
max        1.000000         1.000000        1.000000     1.000000   

       has_agility  has_super_strength  
count  1228.000000         1228.000000  
mean      0.566775            0.522801  
std       0.495723            0.499683  
min       0.000000            0.000000  
25%       0.000000            0.000000  
50%       1.000000            1.000000  
75%       1.000000            1.000000  
max       1.000000            1.000000  

[8 rows x 57 columns]

In [ ]:
dt_to_hists = df_comics.loc[
    :,
    ['name',
    'intelligence_score',
    'strength_score',
    'speed_score',
    'durability_score',
    'power_score',
    'combat_score'
    ],
].melt(id_vars=["name"], var_name="variable", value_name="valor")

px.histogram(
    dt_to_hists, x="valor", color="variable", facet_col="variable", facet_col_wrap=4
).update_layout(showlegend=False)

Las variables que utilizaremos en el futuro tienen comportamientos en sus histogramas muy lejanos a una normal, por lo que usaremos un transformador minmax para normalizarlos.

In [ ]:
from sklearn.preprocessing import MinMaxScaler, Normalizer
from umap import UMAP

projection_pipe = Pipeline(
    [
        (
            "Column Transformer",
            ColumnTransformer(
                [("MinMax", MinMaxScaler(), ['intelligence_score'
                                              ,'strength_score'
                                              ,'speed_score'
                                              ,'durability_score'
                                              ,'power_score'
                                              ,'combat_score'])],
                remainder="passthrough",
            ),
        ),
        ("Normalize", Normalizer()),
        ("UMAP", UMAP(random_state=88, n_neighbors=20, min_dist=0.15)),
    ]
)


projections = projection_pipe.fit_transform(
    df_comics.loc[
        :,
        [
          'intelligence_score',
          'strength_score',
          'speed_score',
          'durability_score',
          'power_score',
          'combat_score'
        ],
    ]
)
df_proj = pd.DataFrame(projections, columns=["x", "y"])

c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\umap\distances.py:1063: NumbaDeprecationWarning:

The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.

c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\umap\distances.py:1071: NumbaDeprecationWarning:

The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.

c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\umap\

In [ ]:
df_fig = df_comics.copy()
df_fig = pd.concat([df_fig, df_proj], axis=1)

fig = px.scatter(
    df_fig,
    x="x",
    y="y",
    color="alignment",
    hover_name="name",
    hover_data=[
          'intelligence_score',
          'strength_score',
          'speed_score',
          'durability_score',
          'power_score',
          'combat_score'
    ],
)
fig.show()

In [ ]:
correlations_df = df_comics[
    [
          'intelligence_score',
          'strength_score',
          'speed_score',
          'durability_score',
          'power_score',
          'combat_score'
    ]
]
correlations = correlations_df.corr()


px.imshow(
    correlations,
    labels=dict(x="", y="", color="Correlation"),
    x=correlations_df.columns,
    y=correlations_df.columns,
    zmin=-1,
    zmax=1,
    color_continuous_scale="Inferno",
)

No se detectaron correlaciones muy marcadas.

## 1.1 Obtención de Features y Bag of Words

<p align="center">
  <img src="https://media0.giphy.com/media/eIUpSyzwGp0YhAMTKr/200.gif" width="300">
</p>

Primero que todo, deben obtener un vector de características del atributo `history_text`, utilizando `Bag of Words`. En este atributo se presenta una breve descripción de la historia de cada uno de los personajes de ficción presentes en el dataset.

Pero... antes de empezar, ¿Que es `Bag of Words`?...

`Bag of Words` es un modelo de conteo utilizado en Procesamiento de Lenguaje Natural (NLP) que tiene como objetivo generar una representación vectorial (vector de características en nuestro cas) para cada documento a través del conteo de las palabras que contienen.

La siguiente figura muestra un ejemplo de `Bag of Words` en acción:

<p align="center">
  <img src="https://user.oc-static.com/upload/2020/10/23/16034397439042_surfin%20bird%20bow.png" width="500">
</p>

Como pueden ver, el modelo de `Bag of Words` no resulta tan complicado, ¿pero cómo lo aplicamos en python?.

Como podrán darse cuenta del ejemplo anterior, para facilitar el conteo será necesario transformar cada uno de los documentos en vectores, donde cada una de las posiciones posee un carácter. Este proceso es conocido como **tokenización** y lo podemos realizar de la siguiente forma:

In [ ]:
docs = ['The teacher rocks like a good rock & roll',
             'the rock is the best actor in the world']


docs_tokenizados = [word_tokenize(doc)  for doc in docs]
docs_tokenizados

[['The', 'teacher', 'rocks', 'like', 'a', 'good', 'rock', '&', 'roll'],
 ['the', 'rock', 'is', 'the', 'best', 'actor', 'in', 'the', 'world']]

Podemos mejorar un poco más el proceso de tokenización agregando

- Stemming:  Definimos Stemming como un algoritmo basado en reglas que transforma las palabras a una forma general. Un ejemplo de stemming, es el siguiente:
- Eliminación de Stopwords: Eliminación de palabras muy frecuentes que entorpecen la clasificación (por ejemplo, el, la los, la, etc...)

<p align="center">
  <img src="https://devopedia.org/images/article/218/8583.1569386710.png" width="300">
</p>


In [ ]:
# Definimos algunas stopword que queremos que sean eliminadas
import nltk
nltk.download('stopwords')

from nltk.corpus import stopwords

stop_words = stopwords.words('english')

# Definimos un tokenizador con Stemming
class StemmerTokenizer:
    def __init__(self):
        self.ps = PorterStemmer()
    def __call__(self, doc):
        doc_tok = word_tokenize(doc)
        doc_tok = [t for t in doc_tok if t not in stop_words]
        return [self.ps.stem(t) for t in doc_tok]

# Inicializamos tokenizador
tokenizador = StemmerTokenizer()

# Creamos algunos documentos
docs = ['The teacher rocks like a good rock & roll',
        'the rock is the best actor in the world',
        'New York is a beautiful city']

# Obtenemos el token del primer documento
[tokenizador(doc) for doc in docs]

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\marti\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


[['the', 'teacher', 'rock', 'like', 'good', 'rock', '&', 'roll'],
 ['rock', 'best', 'actor', 'world'],
 ['new', 'york', 'beauti', 'citi']]

In [ ]:
# Comparación con el caso anterior
docs_tokenizados = [word_tokenize(doc) for doc in docs]
docs_tokenizados

[['The', 'teacher', 'rocks', 'like', 'a', 'good', 'rock', '&', 'roll'],
 ['the', 'rock', 'is', 'the', 'best', 'actor', 'in', 'the', 'world'],
 ['New', 'York', 'is', 'a', 'beautiful', 'city']]

#### Al Estilo Scikit

Scikit implementa `bag of words` a través de la clase `CountVectorizer()` la cual contiene muchas opciones para mejorar la tokenización.

In [ ]:
bow = CountVectorizer(tokenizer= StemmerTokenizer())
df = bow.fit_transform(docs)

pd.DataFrame(df.toarray(), columns=bow.get_feature_names_out())

c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:528: UserWarning:

The parameter 'token_pattern' will not be used since 'tokenizer' is not None'



&  actor  beauti  best  citi  good  like  new  rock  roll  teacher  world  \
0  1      0       0     0     0     1     1    0     2     1        1      0   
1  0      1       0     1     0     0     0    0     1     0        0      1   
2  0      0       1     0     1     0     0    1     0     0        0      0   

   york  
0     0  
1     0  
2     1

Una de las cosas más interesantes que provee son el use de n-gramas, los cuales, en palabras simples, son conjuntos de n-palabras que se concatenan entre si y que se consideran como tokens separados.

Pensemos en `Nueva York`. Cuando se tokeniza Nueva York, se generan dos tokens independientes que a simple vista no tienen relación: `Nueva` `York`.
Al usar n-gramas (en un rango min=1,max=2) , generamos tanto `Nueva` y `York` como también `Nueva York` como un token independiente.

In [ ]:
bow = CountVectorizer(tokenizer= StemmerTokenizer(), ngram_range=(1,2))
df = bow.fit_transform(docs)

pd.DataFrame(df.toarray(), columns=bow.get_feature_names_out())

c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:528: UserWarning:

The parameter 'token_pattern' will not be used since 'tokenizer' is not None'



&  & roll  actor  actor world  beauti  beauti citi  best  best actor  citi  \
0  1       1      0            0       0            0     0           0     0   
1  0       0      1            1       0            0     1           1     0   
2  0       0      0            0       1            1     0           0     1   

   good  ...  rock  rock &  rock best  rock like  roll  teacher  teacher rock  \
0     1  ...     2       1          0          1     1        1             1   
1     0  ...     1       0          1          0     0        0             0   
2     0  ...     0       0          0          0     0        0             0   

   world  york  york beauti  
0      0     0            0  
1      1     0            0  
2      0     1            1  

[3 rows x 25 columns]

De los resultados, podemos ver que generamos vectores de conteo para cada una de las palabras que conforman el corpus.  Un punto extra que se agrega en esta obtención de frecuencias son los bigramas, que básicamente son el conjunto de palabras de tamaño de aparecen juntas en el texto.

## Codificando los Super{heroes, villanos}  [0.5 Puntos]

<p align="center">
  <img src="https://c.tenor.com/LkQzw7k5DV4AAAAd/anime-hacking.gif" width="300">
</p>

Conociendo ahora que es el proceso de `bag of words`, aplique este modelo de obtención de caracteristicas de la siguiente forma en un pipeline:

- Utilice el tokenizador entregado.
- Obtenga caracteristicas de los unigramas y bigramas del texto (tal como el ejemplo).

```python
bog = CountVectorizer(tokenizer= StemmerTokenizer(),`
                      ngram_range=(1,2) # Este punto es opcional y es para generar bigramas
                      )
```

Finalmente, aplique `MinMaxScaler()` sobre `atributos_de_interes` y concatene el valor obtenido con el matriz de caracteristicas obtenidas con bag of words.

```python
atributos_de_interes = ['intelligence_score', 'strength_score', 'speed_score', 'durability_score', 'power_score', 'combat_score']
```

No es necesario que obtenga un dataframe en concreto con las características solicitadas. Se le recomienda generar un `ColumnTransformer()` para aplicar las transformaciones solicitadas en un pipeline.

**To-Do:**
- [ ] Obtener a traves de Bag of Words (`CountVectorizer`) caracteristicas del resumen de historia de cada personaje.
- [ ] Aplicar `MinMaxScaler` sobre los atributos de interes.

**Respuesta:**

In [ ]:
atributos_de_interes = [
    'intelligence_score',
    'strength_score',
    'speed_score',
    'durability_score',
    'power_score',
    'combat_score'
    ]
bag_of_words = [
    'history_text'
    ]

In [ ]:
import re
def preproces(text):
    # Eliminar signos de exclamación y paréntesis, caracteres en otros idioma y otros simbolos.
    text = re.sub(r'[@#_-]|[^\w\s]|[\d]|[^\x00-\x7F]+', '', text)
    return text

In [ ]:
bow = CountVectorizer(tokenizer= StemmerTokenizer(), ngram_range=(1,2), stop_words = 'english', preprocessor = preproces)
df = bow.fit_transform(df_comics['history_text'])

pd.DataFrame(df.toarray(), columns=bow.get_feature_names_out())

c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:528: UserWarning:

The parameter 'token_pattern' will not be used since 'tokenizer' is not None'

c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:409: UserWarning:

Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['afterward', 'alon', 'alreadi', 'alway', 'anoth', 'anyon', 'anyth', 'anywher', 'becam', 'becom', 'besid', 'cri', 'describ', 'els', 'elsewher', 'empti', 'everi', 'everyon', 'everyth', 'everywher', 'fifti', 'formerli', 'forti', 'henc', 'hereaft', 'herebi', 'howev', 'hundr', 'inde', 'latterli', 'mani', 'meanwhil', 'moreov', 'mostli', 'nobodi', 'noon', 'noth', 'nowher', 'otherwis', 'perhap', 'pleas', 'seriou', 'sever', 'sinc', 'sincer', 'sixti', 'someon', 'someth', 'sometim', 'somewher', 'thenc', 'thereaft', 'therebi', 'therefor', 'thu', 'togeth', 'twelv', 'tw

aa  aa alway  aa brik  aa current  aa exchang  aa ideal  aa kworri  \
0      0         0        0           0           0         0          0   
1      0         0        0           0           0         0          0   
2     28         2        2           1           2         1          4   
3      0         0        0           0           0         0          0   
4      0         0        0           0           0         0          0   
...   ..       ...      ...         ...         ...       ...        ...   
1280   0         0        0           0           0         0          0   
1281   0         0        0           0           0         0          0   
1282   0         0        0           0           0         0          0   
1283   0         0        0           0           0         0          0   
1284   0         0        0           0           0         0          0   

      aa new  aa passiv  aa prepar  ...  zzzax reform  zzzax shoot  \
0          0          0          0  ...             0            0   
1          0          0          0  ...             0            0   
2          1          2          2  ...             0            0   
3          0          0          0  ...             0            0   
4          0          0          0  ...             0            0   
...      ...        ...        ...  ...           ...          ...   
1280       0          0          0  ...             0            0   
1281       0          0          0  ...             0            0   
1282       0          0          0  ...             0            0   
1283       0          0          0  ...             0            0   
1284       0          0          0  ...             3            1   

      zzzax shortcircuit  zzzax sinc  zzzax space  zzzax stand  zzzax submerg  \
0                      0           0            0            0              0   
1                      0           0            0            0              0   
2                      0           0            0            0              0   
3                      0           0            0            0              0   
4                      0           0            0            0              0   
...                  ...         ...          ...          ...            ...   
1280                   0           0            0            0              0   
1281                   0           0            0            0              0   
1282                   0           0            0            0              0   
1283                   0           0            0            0              0   
1284                   1           1            1            1              1   

      zzzax tri  zzzax water  zzzax zzzax  
0             0            0            0  
1             0            0            0  
2             0            0            0  
3             0            0            0  
4             0            0            0  
...         ...          ...          ...  
1280          0            0            0  
1281          0            0            0  
1282          0            0            0  
1283          0            0            0  
1284          1            1            1  

[1285 rows x 352823 columns]

In [ ]:
minmax = MinMaxScaler()

preprocess = ColumnTransformer([
                            ('minmax', minmax, atributos_de_interes),
                            ('text_preprocessing', CountVectorizer(tokenizer= StemmerTokenizer()
                                                    , ngram_range=(1,2)
                                                    , stop_words = 'english'
                                                    , preprocessor = preproces), 'history_text')
                        ])
pipeline_preproc = Pipeline([
    ('transform', preprocess)
])


In [ ]:
df_proc = pipeline_preproc.fit_transform(df_comics)

c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['afterward', 'alon', 'alreadi', 'alway', 'anoth', 'anyon', 'anyth', 'anywher', 'becam', 'becom', 'besid', 'cri', 'describ', 'els', 'elsewher', 'empti', 'everi', 'everyon', 'everyth', 'everywher', 'fifti', 'formerli', 'forti', 'henc', 'hereaft', 'herebi', 'howev', 'hundr', 'inde', 'latterli', 'mani', 'meanwhil', 'moreov', 'mostli', 'nobodi', 'noon', 'noth', 'nowher', 'otherwis', 'perhap', 'pleas', 'seriou', 'sever', 'sinc', 'sincer', 'sixti', 'someon', 'someth', 'sometim', 'somewher', 'thenc', 'thereaft', 'therebi', 'therefor', 'thu', 'togeth'

In [ ]:
pd.DataFrame(data = df_proc.toarray(), columns = list(preprocess.get_feature_names_out())).head()

minmax__intelligence_score  minmax__strength_score  minmax__speed_score  \
0                        0.85                     0.3                 0.60   
1                        0.80                     1.0                 0.80   
2                        0.80                     0.5                 0.55   
3                        0.80                     0.1                 0.25   
4                        0.90                     0.4                 0.45   

   minmax__durability_score  minmax__power_score  minmax__combat_score  \
0                      0.60                 0.40                  0.70   
1                      1.00                 1.00                  0.80   
2                      0.45                 1.00                  0.55   
3                      0.40                 0.30                  0.50   
4                      0.55                 0.55                  0.85   

   text_preprocessing__aa  text_preprocessing__aa alway  \
0                     0.0                           0.0   
1                     0.0                           0.0   
2                    28.0                           2.0   
3                     0.0                           0.0   
4                     0.0                           0.0   

   text_preprocessing__aa brik  text_preprocessing__aa current  ...  \
0                          0.0                             0.0  ...   
1                          0.0                             0.0  ...   
2                          2.0                             1.0  ...   
3                          0.0                             0.0  ...   
4                          0.0                             0.0  ...   

   text_preprocessing__zzzax reform  text_preprocessing__zzzax shoot  \
0                               0.0                              0.0   
1                               0.0                              0.0   
2                               0.0                              0.0   
3                               0.0                              0.0   
4                               0.0                              0.0   

   text_preprocessing__zzzax shortcircuit  text_preprocessing__zzzax sinc  \
0                                     0.0                             0.0   
1                                     0.0                             0.0   
2                                     0.0                             0.0   
3                                     0.0                             0.0   
4                                     0.0                             0.0   

   text_preprocessing__zzzax space  text_preprocessing__zzzax stand  \
0                              0.0                              0.0   
1                              0.0                              0.0   
2                              0.0                              0.0   
3                              0.0                              0.0   
4                              0.0                              0.0   

   text_preprocessing__zzzax submerg  text_preprocessing__zzzax tri  \
0                                0.0                            0.0   
1                                0.0                            0.0   
2                                0.0                            0.0   
3                                0.0                            0.0   
4                                0.0                            0.0   

   text_preprocessing__zzzax water  text_preprocessing__zzzax zzzax  
0                              0.0                              0.0  
1                              0.0                              0.0  
2                              0.0                              0.0  
3                              0.0                              0.0  
4                              0.0                              0.0  

[5 rows x 352829 columns]

## 1.2 Diseño de Baseline y  Primer Entrenamiento  [1 Puntos]


<p align="center">
  <img src="https://pa1.narvii.com/6374/9eaec1b7bf9157334151452a669516f9a78b954c_hq.gif" width="300">
</p>



Genere un Pipeline con las caracteristicas solicitadas en la sección 1.1, un selector de mejores features `SelectPercentile` con métrica `f_classif` y percentile=90 y un clasificador `MultinomialNB()` por defecto.

Luego, separe el conjunto de datos en un conjunto de entrenamiento y prueba, donde las etiquetas estará dado por el atributo `alignment`.

Entrene el modelo y reporte el desempeño con un `classification_report`. ¿ Nos recomendaría predecir la alineación de BatCow con este clasificador?.

Finalmente, compare el modelo entrenado con un modelo Dummy estratificado y responda: ¿El clasificador entrenado es mejor que el dummy que entrega respuestas al azar?

**To-do:**
- [ ] Realizar un pipeline con las caracteristicas solicitadas en 1.1, ejecutar holdout y aplicar un clasificador `MultinomialNB()`.
- [ ] Entrenar el pipeline, calcular el `classification_report` asociado y comentar los resultados.
- [ ] Entrenar un `DummyClassifier` con estrategia `statified`, calcular el `classification_report` asociado y comentar que implican los scores obtenidos en comparación con los resultados del baseline.

**Respuesta:**

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(df_comics, df_comics['alignment'], test_size=0.3, random_state=23)

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.feature_selection import SelectPercentile, f_classif
from sklearn.naive_bayes import MultinomialNB

# Crear el Pipeline
pipeline = Pipeline([
    ('scaler', preprocess),
    ('feature_selection', SelectPercentile(score_func=f_classif, percentile=90)),
    ('classification', MultinomialNB())
])

# Entrenar el Pipeline
pipeline.fit(X_train, y_train)

y_pred = pipeline.predict(X_test)


c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['afterward', 'alon', 'alreadi', 'alway', 'anoth', 'anyon', 'anyth', 'anywher', 'becam', 'becom', 'besid', 'cri', 'describ', 'els', 'elsewher', 'empti', 'everi', 'everyon', 'everyth', 'everywher', 'fifti', 'formerli', 'forti', 'henc', 'hereaft', 'herebi', 'howev', 'hundr', 'inde', 'latterli', 'mani', 'meanwhil', 'moreov', 'mostli', 'nobodi', 'noon', 'noth', 'nowher', 'otherwis', 'perhap', 'pleas', 'seriou', 'sever', 'sinc', 'sincer', 'sixti', 'someon', 'someth', 'sometim', 'somewher', 'thenc', 'thereaft', 'therebi', 'therefor', 'thu', 'togeth'

In [ ]:
print(classification_report(y_pred=y_pred, y_true=y_test))

              precision    recall  f1-score   support

         Bad       0.72      0.26      0.38       121
        Good       0.64      0.96      0.77       227
     Neutral       0.67      0.05      0.10        38

    accuracy                           0.65       386
   macro avg       0.68      0.42      0.42       386
weighted avg       0.67      0.65      0.58       386



Vemos que nuestro clasificador no obtiene buenos resultados, sus metricas son muy malas, tiende a predecir bueno con demasiada frecuencia, la cual es la clase mayoritaria, generando muy malas predicciones para las otras 2 clases, las cuales tienen recalls bajisimos. Este clasificador no entregara una buena predicción y tendera a asignar la clase good a las nuevas muestras. Podemos culpar de estos resultados a el resultado la construcción de los vectores de bags of word, cuyo resultado nos dejo con más de 350.000 columnas para solo 1.300 datos

In [ ]:
from sklearn.dummy import DummyClassifier

dummy_clf = DummyClassifier(strategy="stratified")

pipeline2 = Pipeline([
    ('scaler', preprocess),
    ('feature_selection', SelectPercentile(score_func=f_classif, percentile=90)),
    ('classification', dummy_clf)
])

# Entrenar el Pipeline
pipeline2.fit(X_train, y_train)

y_pred2 = pipeline2.predict(X_test)

/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:112: UserWarning: Features [    23     24     25 ... 352781 352782 352783] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:113: RuntimeWarning: invalid value encountered in true_divide
  f = msb / msw


In [ ]:
print(classification_report(y_pred=y_pred2, y_true=y_test))

              precision    recall  f1-score   support

         Bad       0.33      0.40      0.36       121
        Good       0.58      0.53      0.56       227
     Neutral       0.06      0.05      0.06        38

    accuracy                           0.44       386
   macro avg       0.32      0.33      0.32       386
weighted avg       0.45      0.44      0.45       386



El clasificador dummy obtiene peores resultados que el primero, malisima precisión y recall en todas las clases. Almenos podemos decir que nuestro modelo funciona mejor que lanzar los valores de manera aleatoria.

## 1.3 Busqueda del Mejor Modelo con Grid Search [4 Puntos]

<p align="center">
  <img src="https://media1.tenor.com/images/70fdfeea52a8e2e4505498c230a0d2f9/tenor.gif?itemid=5134219" width="250">
</p>

No conformes con el rendimiento obtenido en la sección 1.2, el cuerpo docente les pide que realicen un **`HalvingGridSearchCV`** con diferentes parámetros para mejorar el rendimiento de la clasificación. Para esto, se le solicita que defina:

- Tres clasificadores distintos en donde varie sus parámetros. Considere usar modelos clásicos como también los basados en ensamblaje.
- Modificar `n-gram` range del `CountVectorizer` probando `(1,1), (1,2) y (1,3)`. Examinar también los otros parámetros de CountVectorizer como por ejemplo `max_df`, `min_df`, etc... ([Documentación aquí](https://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.CountVectorizer.html))
- Seleccionar las columnas que contribuyen con la mayor información para la clasificación con `SelectPercentile` en los percentiles `[20, 40, 60, 80]` (puede usar la métrica que usted quiera).
- Reporte la mejor combinación encontrada y justifique por qué cree que es la mejor según el clasificador usado, la cantidad de columnas seleccionadas y los parámetros de CountVectorizer seleccionados por GridSearch.

A continuación, un ejemplo de parametros para GridSearch para una búsqueda de 3 clasificadores distintos:

```python
params = [
       # clasificador 1 + hiperparámetros
       {'clf': classificator1(),
        'clf__penalty': ['ovr'],
       # clasificador 1 + hiperparámetros
       {'clf': classificator2(),
        'clf__n_estimators': [200]},
       # clasificador 1 + hiperparámetros
       {'clf': classificator3(),
        ...
       }
       ]
```

**Nota 1**: Puede ver los parámetros modificables aplicando el método get_params() sobre su pipeline. Ver la clase de GridSearch para mayor información sobre la sintáxis de las grillas.

**Nota 2**: Recuerde inicializar los clasificadores con un random state definido.

**Nota 3**: Puede usar en `HalvingGridSearchCV` el parámetro `verbose=10` para ver que GridSearch le indique el estado de su ejecución.

**Nota 3:** El GridSearch puede tomar tiempos de búsqueda exorbitantes, por lo que se le recomienda no agrandar mucho el espacio de búsqueda, dejar corriendo el código y tomarse un tecito.

**Respuesta:**

In [ ]:
from sklearn.ensemble import HistGradientBoostingClassifier
from sklearn.experimental import enable_halving_search_cv
from sklearn.model_selection import HalvingGridSearchCV

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(df_comics, df_comics['alignment'], test_size=0.3, random_state=23)

In [ ]:
text_preprocessing = Pipeline([
    ( 'count_vectorizer', CountVectorizer(tokenizer= StemmerTokenizer()
                                                    , ngram_range = (1,1)
                                                    , stop_words = 'english'
                                                    , preprocessor = preproces)
                                                    )])

preprocess = ColumnTransformer([
                            ('minmax', minmax, atributos_de_interes),
                            ('text_preprocessing', CountVectorizer(tokenizer= StemmerTokenizer(), stop_words = 'english', preprocessor = preproces), 'history_text')
                        ])

In [ ]:
pipe1 = Pipeline([
    ('scaler', preprocess),
    ('feature_selection', SelectPercentile(score_func=f_classif)),
    ('classifier', MultinomialNB())
])

# Definir los parámetros a ajustar en la búsqueda en cuadrícula
param_grid_1 = [
    {
    'scaler__text_preprocessing__ngram_range': [(1,1), (1,2), (1,3)],
    'scaler__text_preprocessing__max_df': [1, 0.9, 0.8, 0.7],
    'scaler__text_preprocessing__min_df': [0, 0.1, 0.2, 0.3],
    'feature_selection__percentile': [20, 40, 60, 80]
    }
]

Los Modelos que tulizaremos serán NaiveBayes clásico, usaremos un random Forest y por ultimo un HistGradientBoosting. Para mejorar el perfomance y reducir los tiempos de esperar (collab a veces se caia antes de termianr) es que no incluiremos el cambio de modelos en la grilla y los haremos por separado. Compararemos los resultados de las 3 grillas y decidiremos cual fue el mejor modelo.

In [ ]:
grid_search1 = HalvingGridSearchCV(pipe1, param_grid_1, scoring='accuracy', verbose = 10)
grid_search1.fit(X_train, y_train)

In [ ]:
grid_search1.best_params_

{'feature_selection__percentile': 60,
 'scaler__text_preprocessing__max_df': 0.9,
 'scaler__text_preprocessing__min_df': 0,
 'scaler__text_preprocessing__ngram_range': (1, 1)}

In [ ]:
import csv

# Obtener los mejores parámetros
best_params = grid_search1.best_params_

# Guardar los mejores parámetros en un archivo CSV
csv_file = 'best_params1.csv'
with open(csv_file, 'w', newline='') as file:
    writer = csv.DictWriter(file, fieldnames=best_params.keys())
    writer.writeheader()
    writer.writerow(best_params)


In [ ]:
y_pred1 = grid_search1.predict(X_test)
print(classification_report(y_pred=y_pred1, y_true=y_test))

              precision    recall  f1-score   support

         Bad       0.58      0.54      0.56       121
        Good       0.71      0.81      0.76       227
     Neutral       0.33      0.16      0.21        38

    accuracy                           0.66       386
   macro avg       0.54      0.50      0.51       386
weighted avg       0.64      0.66      0.64       386



El resultado de Naive Bayes usando la grilla mejora solo un poco, su accuracy llego hasta 0.66, sólo un poco mejor que la versión anterior sin la grilla, sin mebargo obtiene un macro average mucho mejor, que para clases desbalanceadas como estas funciona mejor como estimador.

Los mejores parametros indican que el mejor resultado se alcanzo con el 60%, eliminandose el 10% de las palabras más frecuentes y los ngramas usando sólo de tamaño 1.

In [ ]:
pipe2 = Pipeline(
    [('scaler', preprocess),
     ('feature_selection', SelectPercentile(score_func=f_classif)),
     ('classifier', RandomForestClassifier(random_state = 23))
    ])

param_grid_2 = {
    'scaler__text_preprocessing__ngram_range': [(1,1), (1,2), (1,3)],
    'scaler__text_preprocessing__max_df': [0.9, 0.8],
    'scaler__text_preprocessing__min_df': [0.1, 0.2],
    'feature_selection__percentile': [20, 40, 60, 80],
    'classifier__n_estimators': [10, 50, 100],
    'classifier__max_depth': [5, 10, 15]
}

In [ ]:
grid_search2 = HalvingGridSearchCV(pipe2, param_grid_2, scoring='accuracy')
grid_search2.fit(X_train, y_train)

c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['afterward', 'alon', 'alreadi', 'alway', 'anoth', 'anyon', 'anyth', 'anywher', 'becam', 'becom', 'besid', 'cri', 'describ', 'els', 'elsewher', 'empti', 'everi', 'everyon', 'everyth', 'everywher', 'fifti', 'formerli', 'forti', 'henc', 'hereaft', 'herebi', 'howev', 'hundr', 'inde', 'latterli', 'mani', 'meanwhil', 'moreov', 'mostli', 'nobodi', 'noon', 'noth', 'nowher', 'otherwis', 'perhap', 'pleas', 'seriou', 'sever', 'sinc', 'sincer', 'sixti', 'someon', 'someth', 'sometim', 'somewher', 'thenc', 'thereaft', 'therebi', 'therefor', 'thu', 'togeth'

HalvingGridSearchCV(estimator=Pipeline(steps=[('scaler',
                                               ColumnTransformer(transformers=[('minmax',
                                                                                MinMaxScaler(),
                                                                                ['intelligence_score',
                                                                                 'strength_score',
                                                                                 'speed_score',
                                                                                 'durability_score',
                                                                                 'power_score',
                                                                                 'combat_score']),
                                                                               ('text_preprocessing',
                                                                                CountVectorizer(preprocessor=<function preproces at 0x0000020DFED832E0>,
                                                                                                stop_words='english',
                                                                                                tokenizer=<__main__.St...
                                               RandomForestClassifier(random_state=23))]),
                    param_grid={'classifier__max_depth': [5, 10, 15],
                                'classifier__n_estimators': [10, 50, 100],
                                'feature_selection__percentile': [20, 40, 60,
                                                                  80],
                                'scaler__text_preprocessing__max_df': [0.9,
                                                                       0.8],
                                'scaler__text_preprocessing__min_df': [0.1,
                                                                       0.2],
                                'scaler__text_preprocessing__ngram_range': [(1,
                                                                             1),
                                                                            (1,
                                                                             2),
                                                                            (1,
                                                                             3)]},
                    scoring='accuracy')

In [ ]:
# Obtener los mejores parámetros
best_params = grid_search2.best_params_

# Guardar los mejores parámetros en un archivo CSV
csv_file = 'best_params2.csv'
with open(csv_file, 'w', newline='') as file:
    writer = csv.DictWriter(file, fieldnames=best_params.keys())
    writer.writeheader()
    writer.writerow(best_params)

In [ ]:
grid_search2.best_params_

{'classifier__max_depth': 10,
 'classifier__n_estimators': 50,
 'feature_selection__percentile': 60,
 'scaler__text_preprocessing__max_df': 0.9,
 'scaler__text_preprocessing__min_df': 0.1,
 'scaler__text_preprocessing__ngram_range': (1, 2)}

In [ ]:
y_pred2 = grid_search2.predict(X_test)
print(classification_report(y_pred=y_pred2, y_true=y_test))


              precision    recall  f1-score   support

         Bad       0.55      0.19      0.28       121
        Good       0.63      0.96      0.76       227
     Neutral       0.50      0.03      0.05        38

    accuracy                           0.62       386
   macro avg       0.56      0.39      0.36       386
weighted avg       0.59      0.62      0.54       386



Para el caso del modelo de Random Forest, vemos que la mejor combinación logro un accuracy de 0,62 el cual es menor que el obtenido por el modelo de NB.

Los mejores parametros para el caso del arbol incluyen tambien un largo maximo de los arboles, el cual se obtuvo con 10 el percentil de columnas seleccionadas tambien fue de 60%, eliminandose el 10% de las palabras más frecuentesy tambien el 10% de las palabras menos fecuentes. Por ultimo los ngramas se utilizo hasta ngramas de 2 palabras.

In [ ]:
pipe3 = Pipeline(
    [('Preprocesamiento', preprocess),
     ('feature_selection', SelectPercentile(score_func=f_classif)),
     ('HistGradientBoostingClassifier', HistGradientBoostingClassifier(
         random_state=23,
         max_iter=1000))
    ])

param_grid_3 = {
    'Preprocesamiento__text_preprocessing__ngram_range': [(1,1), (1,2), (1,3)],
    'Preprocesamiento__text_preprocessing__max_df': [0.9, 0.8],
    'Preprocesamiento__text_preprocessing__min_df': [0.1, 0.2],
    'feature_selection__percentile': [20, 40, 60, 80],
    'HistGradientBoostingClassifier__l2_regularization': [0.1, 1],
    'HistGradientBoostingClassifier__max_depth': [5, 10, 15]
}


In [ ]:
grid_search3 = HalvingGridSearchCV(pipe3, param_grid_3, scoring='accuracy')
grid_search3.fit(X_train, y_train)

c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['afterward', 'alon', 'alreadi', 'alway', 'anoth', 'anyon', 'anyth', 'anywher', 'becam', 'becom', 'besid', 'cri', 'describ', 'els', 'elsewher', 'empti', 'everi', 'everyon', 'everyth', 'everywher', 'fifti', 'formerli', 'forti', 'henc', 'hereaft', 'herebi', 'howev', 'hundr', 'inde', 'latterli', 'mani', 'meanwhil', 'moreov', 'mostli', 'nobodi', 'noon', 'noth', 'nowher', 'otherwis', 'perhap', 'pleas', 'seriou', 'sever', 'sinc', 'sincer', 'sixti', 'someon', 'someth', 'sometim', 'somewher', 'thenc', 'thereaft', 'therebi', 'therefor', 'thu', 'togeth'

HalvingGridSearchCV(estimator=Pipeline(steps=[('Preprocesamiento',
                                               ColumnTransformer(transformers=[('minmax',
                                                                                MinMaxScaler(),
                                                                                ['intelligence_score',
                                                                                 'strength_score',
                                                                                 'speed_score',
                                                                                 'durability_score',
                                                                                 'power_score',
                                                                                 'combat_score']),
                                                                               ('text_preprocessing',
                                                                                CountVectorizer(preprocessor=<function preproces at 0x0000020DFED832E0>,
                                                                                                stop_words='english',
                                                                                                tokenizer=<_...
                    param_grid={'HistGradientBoostingClassifier__l2_regularization': [0.1,
                                                                                      1],
                                'HistGradientBoostingClassifier__max_depth': [5,
                                                                              10,
                                                                              15],
                                'Preprocesamiento__text_preprocessing__max_df': [0.9,
                                                                                 0.8],
                                'Preprocesamiento__text_preprocessing__min_df': [0.1,
                                                                                 0.2],
                                'Preprocesamiento__text_preprocessing__ngram_range': [(1,
                                                                                       1),
                                                                                      (1,
                                                                                       2),
                                                                                      (1,
                                                                                       3)],
                                'feature_selection__percentile': [20, 40, 60,
                                                                  80]},
                    scoring='accuracy')

In [ ]:
# Obtener los mejores parámetros
best_params = grid_search3.best_params_

# Guardar los mejores parámetros en un archivo CSV
csv_file = 'best_params3.csv'
with open(csv_file, 'w', newline='') as file:
    writer = csv.DictWriter(file, fieldnames=best_params.keys())
    writer.writeheader()
    writer.writerow(best_params)

In [ ]:
grid_search3.best_params_

{'HistGradientBoostingClassifier__l2_regularization': 1,
 'HistGradientBoostingClassifier__max_depth': 15,
 'Preprocesamiento__text_preprocessing__max_df': 0.8,
 'Preprocesamiento__text_preprocessing__min_df': 0.2,
 'Preprocesamiento__text_preprocessing__ngram_range': (1, 3),
 'feature_selection__percentile': 80}

In [ ]:
y_pred3 = grid_search3.predict(X_test)
print(classification_report(y_pred=y_pred3, y_true=y_test))

              precision    recall  f1-score   support

         Bad       0.45      0.46      0.46       121
        Good       0.69      0.74      0.71       227
     Neutral       0.29      0.13      0.18        38

    accuracy                           0.59       386
   macro avg       0.48      0.44      0.45       386
weighted avg       0.57      0.59      0.58       386



Nuestro ultimo modelo fue el que tuvo los peores resultados, en este caso los parametros fueron los más diferentes, se selecciono el 80% de las caracteristicas más importantes, se elimino el 20% de las palabras más frecuentes y el 20% de las menos frecuentes. Por ultimo uso ngramas de hasta 3 palabras.

## 1.4 Predicción del datos sin etiquetado  [0.5 puntos]

<p align="center">
  <img src="https://pbs.twimg.com/media/DolotxUUYAAbg7f.jpg" width="350">
</p>


LLego el momento de predecir
`Vergil`, `Gorilla Girl` y `Batcow`


**Nota:** Recuerde que pueden existir campos vacios en `history_text`, por lo que se les recomienda borrar los nan.

**Respuesta:**

In [ ]:
preprocess_optim = ColumnTransformer([
                            ('minmax', minmax, atributos_de_interes),
                            ('text_preprocessing', CountVectorizer(tokenizer= StemmerTokenizer(), stop_words = 'english', preprocessor = preproces, max_df = 0.9, min_df = 0), 'history_text')
                        ])

pipe_optim = Pipeline([
    ('scaler', preprocess_optim),
    ('feature_selection', SelectPercentile(score_func=f_classif, percentile = 60)),
    ('classifier', MultinomialNB())
])

In [ ]:
df_comics_no_label_clean = df_comics_no_label.dropna(subset = [
    'intelligence_score',
    'strength_score',
    'speed_score',
    'durability_score',
    'power_score',
    'combat_score',
    'history_text'
    ])

In [ ]:
pipe_optim.fit(X_train, y_train)
y_pred_no_label = pipe_optim.predict(df_comics_no_label_clean)

c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
c:\Users\marti\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\feature_extraction\text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['afterward', 'alon', 'alreadi', 'alway', 'anoth', 'anyon', 'anyth', 'anywher', 'becam', 'becom', 'besid', 'cri', 'describ', 'els', 'elsewher', 'empti', 'everi', 'everyon', 'everyth', 'everywher', 'fifti', 'formerli', 'forti', 'henc', 'hereaft', 'herebi', 'howev', 'hundr', 'inde', 'latterli', 'mani', 'meanwhil', 'moreov', 'mostli', 'nobodi', 'noon', 'noth', 'nowher', 'otherwis', 'perhap', 'pleas', 'seriou', 'sever', 'sinc', 'sincer', 'sixti', 'someon', 'someth', 'sometim', 'somewher', 'thenc', 'thereaft', 'therebi', 'therefor', 'thu', 'togeth'

In [ ]:
df_respuesta = pd.DataFrame(df_comics_no_label_clean['name'])
df_respuesta['prediccion'] = y_pred_no_label

In [ ]:
df_respuesta[df_respuesta['name'].isin(['Vergil', 'Gorilla Girl', 'Batcow'])]

name prediccion
16        Batcow       Good
40  Gorilla Girl        Bad
78        Vergil    Neutral
83        Batcow       Good

Finalmente usando nuestro mejor modelo obtenemos los resultados y vemos que batcow se encuentra en el lado de los buenos =)

<p align="center">
  <img src="https://media1.tenor.com/images/fb5bf7cc5a4acb91b4177672886a88ba/tenor.gif?itemid=5591338">
</p>

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=87110296-876e-426f-b91d-aaf681223468' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>